# Imports, loading

In [1]:
import pandas as pd
import numpy as np
import scipy.sparse as sps
import matplotlib.pyplot as pyplot
import Utils.DataReader as dr
from Evaluation.Evaluator import EvaluatorHoldout

# Specialized on cold and warm users

In [1]:
import pandas as pd
import numpy as np
import scipy.sparse as sps
import matplotlib.pyplot as pyplot
import time
import RecSys2022.Utils.DataReader as dr


from Evaluation.Evaluator import EvaluatorHoldout
from Data_manager.split_functions.split_train_validation_random_holdout import split_train_in_two_percentage_global_sample
from Utils.DataReader import load_urm#, load_icm, load_target
from Recommenders.SLIM.Cython.SLIM_BPR_Cython import UserSlimBPRRecommender
from Recommenders.IR_feature_weighting import okapi_BM_25

from Recommenders.SLIM.SLIMElasticNetRecommender import SLIMElasticNetRecommender
from Recommenders.GraphBased.RP3betaRecommender import UserRP3betaRecommender, RP3betaRecommender
URM_all = dr.load_urm("../data/URMtries/RatingsBinary.csv")
ICM_tr = dr.load_icm("../data/data_ICM_type_truncated.csv")

URM_train = sps.load_npz("trainDefault.npz")
URM_valid = sps.load_npz("validDefault.npz")
evaluator_validation = EvaluatorHoldout(URM_valid, cutoff_list=[10])
stacked_URM = sps.vstack([URM_all, ICM_tr.T])
stacked_URM_train = sps.vstack([URM_train, ICM_tr.T])

from Recommenders.BaseRecommender import BaseRecommender

class DifferentLossScoresHybridRecommender(BaseRecommender):
    """ ScoresHybridRecommender
    Hybrid of three predictions scores
    R = R1*alpha + R2*beta

    Class from Dacrema exercise modified by Antonio Ercolani
    The original took as input 2 recommender

    """

    RECOMMENDER_NAME = "DifferentLossScoresHybridRecommender"

    def __init__(self, URM_train, recommender_1, recommender_2):
        super(DifferentLossScoresHybridRecommender, self).__init__(URM_train)

        self.URM_train = sps.csr_matrix(URM_train)
        self.recommender_1 = recommender_1
        self.recommender_2 = recommender_2

    def fit(self, alpha=0.5, beta=0.5):
        self.alpha = alpha
        self.beta = beta

    def _compute_item_score(self, user_id_array, items_to_compute = None):
        item_weights_1 = self.recommender_1._compute_item_score(user_id_array)
        item_weights_2 = self.recommender_2._compute_item_score(user_id_array)

        item_weights = item_weights_1 * self.alpha + item_weights_2 * self.beta

        return item_weights

#20.42.95.202

EvaluatorHoldout: Ignoring 963 ( 2.3%) Users that have less than 1 test interactions


In [2]:
from Recommenders.SLIM.SLIMElasticNetRecommender import SLIMElasticNetRecommender
recommender_SLIMElStandard = SLIMElasticNetRecommender(stacked_URM_train)
recommender_SLIMElStandard.load_model(
    folder_path= "C:\\Users\\Andrea\\AppData\\Roaming\\JetBrains\\DataSpell2022.2\\projects\\RecSys2022\\data\\saved_models",
    file_name= recommender_SLIMElStandard.RECOMMENDER_NAME + "-trainStack"
)
recommender_SLIMElStandard.W_sparse = recommender_SLIMElStandard.W_sparse.get('W_sparse')

SLIMElasticNetRecommender: URM Detected 3 ( 0.0%) users with no interactions.
SLIMElasticNetRecommender: Loading model from file 'C:\Users\Andrea\AppData\Roaming\JetBrains\DataSpell2022.2\projects\RecSys2022\data\saved_modelsSLIMElasticNetRecommender-trainStack'
  (0, 6)	0.008402271
  (0, 18)	0.0063224747
  (0, 47)	0.003607275
  (0, 135)	0.005423102
  (0, 147)	0.0049014674
  (0, 171)	0.004886132
  (0, 213)	0.00013499164
  (0, 235)	0.003229967
  (0, 306)	0.005453025
  (0, 315)	0.001751438
  (0, 320)	0.0023006063
  (0, 328)	0.011077219
  (0, 329)	0.0025967485
  (0, 335)	0.0048150625
  (0, 350)	0.0039249766
  (0, 441)	0.0012208363
  (0, 472)	0.0012753735
  (0, 491)	0.001108485
  (0, 533)	0.0053392467
  (0, 609)	0.000855769
  (0, 623)	0.0009474329
  (0, 676)	0.0143642705
  (0, 730)	0.0013713039
  (0, 750)	0.0060308203
  (0, 760)	0.0038346748
  :	:
  (24506, 22717)	0.0011144527
  (24506, 23022)	0.0026768818
  (24506, 23047)	0.008131734
  (24506, 23114)	0.002386969
  (24506, 23121)	0.0029612

In [3]:
recommender_SLIMElCold = SLIMElasticNetRecommender(stacked_URM_train)
recommender_SLIMElCold.load_model(
    folder_path= "C:\\Users\\Andrea\\AppData\\Roaming\\JetBrains\\DataSpell2022.2\\projects\\RecSys2022\\data\\saved_models",
    file_name= recommender_SLIMElStandard.RECOMMENDER_NAME + "-trainColdStack"
)
recommender_SLIMElCold.W_sparse = recommender_SLIMElCold.W_sparse.get('W_sparse')

SLIMElasticNetRecommender: URM Detected 3 ( 0.0%) users with no interactions.
SLIMElasticNetRecommender: Loading model from file 'C:\Users\Andrea\AppData\Roaming\JetBrains\DataSpell2022.2\projects\RecSys2022\data\saved_modelsSLIMElasticNetRecommender-trainColdStack'
  (0, 6)	0.003078759
  (0, 18)	0.0017472019
  (0, 47)	0.0015083627
  (0, 135)	0.0020276478
  (0, 147)	0.0023150283
  (0, 171)	0.00168239
  (0, 235)	0.0015507787
  (0, 306)	0.0019492422
  (0, 315)	0.0009951284
  (0, 320)	0.0011242094
  (0, 328)	0.003048607
  (0, 329)	0.0012218966
  (0, 335)	0.0021404931
  (0, 350)	0.0015896612
  (0, 441)	0.0010020413
  (0, 472)	0.0013421976
  (0, 491)	0.0010322504
  (0, 533)	0.001677548
  (0, 609)	0.0012354673
  (0, 623)	0.0009031798
  (0, 676)	0.004287647
  (0, 750)	0.002919926
  (0, 760)	0.0014920838
  (0, 792)	0.001298699
  (0, 822)	0.001125081
  :	:
  (24506, 24106)	0.00014126583
  (24506, 24122)	0.00014568756
  (24506, 24144)	0.0018967893
  (24506, 24146)	0.0010839693
  (24506, 24166)	0

In [4]:
NOF_GROUPS = 3
profile_length = np.ediff1d(sps.csr_matrix(URM_train).indptr)
block_size = int(len(profile_length)*(1/NOF_GROUPS))
sorted_users = np.argsort(profile_length)

group_id = 0
start_pos = group_id*block_size
end_pos = min((group_id+1)*block_size, len(profile_length))

users_in_group = sorted_users[start_pos:end_pos]

users_in_group_p_len = profile_length[users_in_group]

print("Group {}, #users in group {}, average p.len {:.2f}, median {}, min {}, max {}".format(
    group_id,
    users_in_group.shape[0],
    users_in_group_p_len.mean(),
    np.median(users_in_group_p_len),
    users_in_group_p_len.min(),
    users_in_group_p_len.max()))


users_not_in_group_flag = np.isin(sorted_users, users_in_group, invert=True)
users_not_in_group = sorted_users[users_not_in_group_flag]

#evaluator_validation = EvaluatorHoldout(URM_valid,  cutoff_list=[10])
#res, _ = evaluator_validation.evaluateRecommender(recommender_SLIMElCold)
#res.loc[10]["MAP"]

Group 0, #users in group 13876, average p.len 15.68, median 16.0, min 4, max 20


In [21]:
from RecSys2022.Recommenders.SpecializedRecommender import SpecializedRecommender

rp3cold = RP3betaRecommender(stacked_URM_train)
rp3cold.fit(topK= 262, alpha= 0.9421494305982036, beta= 0.30682805926783363, normalize_similarity= True)

rp3generic = RP3betaRecommender(stacked_URM_train)
rp3generic.fit(alpha= 1.0, beta= 0.3168683362512345, topK= 50, implicit= False)

recommender_Specialized_rp3 = SpecializedRecommender(URM_train= stacked_URM_train, recommenderCold= rp3cold, recommenderStandard= rp3generic)
recommender_Specialized_rp3.fit(user_in_cold= users_in_group)

RP3betaRecommender: URM Detected 3 ( 0.0%) users with no interactions.
RP3betaRecommender: Similarity column 24507 (100.0%), 1999.06 column/sec. Elapsed time 12.26 sec
RP3betaRecommender: URM Detected 3 ( 0.0%) users with no interactions.
RP3betaRecommender: Similarity column 24507 (100.0%), 3030.08 column/sec. Elapsed time 8.09 sec
SpecializedRecommender: URM Detected 3 ( 0.0%) users with no interactions.
cold users:
[41083 37420 38400 ... 15529 14880 27309]


In [5]:
from RecSys2022.Recommenders.SpecializedRecommender import SpecializedRecommender

recommender_Specialized = SpecializedRecommender(URM_train= stacked_URM_train, recommenderCold= recommender_SLIMElCold, recommenderStandard= recommender_SLIMElStandard)
recommender_Specialized.fit(user_in_cold= users_in_group)

SpecializedRecommender: URM Detected 3 ( 0.0%) users with no interactions.
cold users:
[41083 37420 38400 ... 15529 14880 27309]


In [11]:
41083 in users_in_group #200 is cold

True

In [8]:
0 in users_in_group #0 is warm

False

In [10]:
200 not in users_not_in_group #200 not in warm

True

In [11]:
0 not in users_in_group #0 not in cold

True

In [13]:
recommender_SLIMElStandard.recommend(41083, cutoff=10)

[2523, 12856, 17505, 2522, 3343, 105, 2722, 36, 520, 2720]

In [12]:
recommender_SLIMElCold.recommend(41083, cutoff=10)

[2523, 12856, 17505, 2522, 3343, 2722, 36, 105, 2720, 520]

In [7]:
recommender_Specialized.recommend(0, cutoff=10)

recommending items to users:  0
using the generic recommender
recommendations: 
[617, 752, 18484, 29, 391, 2488, 2792, 673, 2495, 20]


[[617, 752, 18484, 29, 391, 2488, 2792, 673, 2495, 20]]

In [27]:
evaluator_validation = EvaluatorHoldout(URM_valid, cutoff_list=[10])
res,_ = evaluator_validation.evaluateRecommender(recommender_Specialized_rp3)
res.loc[10]["MAP"] #023411206389799755
#specialized on all: 025803048879020705
#rp3cold on cold: 007494360176734405, on all: 02339645790446159
#rp3generic on cold: 007000213366321161, on all: 02577431402075988
#specialized on cold: 007494360176734405, on all: 023411206389799755

EvaluatorHoldout: Ignoring 963 ( 2.3%) Users that have less than 1 test interactions
recommending items to users:  [   0    1    2    3    4    5    6    7    8    9   10   11   12   13
   14   15   16   17   18   19   20   21   22   23   24   25   26   27
   28   29   30   31   32   33   34   35   36   37   38   39   40   41
   42   43   45   46   47   48   49   50   51   52   53   54   55   56
   57   58   59   60   61   62   63   64   65   66   67   68   69   70
   71   72   73   74   75   76   77   78   79   80   81   82   83   84
   85   86   87   88   89   90   91   92   93   94   95   96   97   98
   99  100  101  102  103  104  105  106  107  108  109  110  111  112
  113  114  115  116  117  118  119  120  121  122  123  124  125  126
  127  128  129  130  131  132  133  134  135  136  137  138  139  140
  142  143  144  145  146  147  148  149  150  151  152  153  154  155
  156  157  158  159  160  161  162  163  164  165  166  167  168  169
  170  171  172  173  174  175  1

0.023411206389799755

In [ ]:
evaluator_validation.evaluateRecommender(recommender_SLIMElStandard)

In [9]:
test_users = pd.read_csv('./data/data_target_users_test.csv')
user_id = test_users['user_id']
recommendations = []
for user in user_id:
    recommendations.append(recommender_Specialized.recommend(user, cutoff=10, return_scores=False))
for index in range(len(recommendations)):
    recommendations[index]=np.array(recommendations[index])

test_users['item_list']= recommendations
test_users['item_list'] = pd.DataFrame([str(line).strip('[').strip(']').replace("'","") for line in test_users['item_list']])
test_users.to_csv('special_slim.csv', index=False)

recommending items to users:  0
using the generic recommender
recommendations: 
[617, 752, 18484, 29, 391, 2488, 2792, 673, 2495, 20]
recommending items to users:  1
using the cold recommender
recommendations: 
[6874, 1068, 393, 62, 56, 60, 61, 665, 23, 270]
recommending items to users:  2
using the generic recommender
recommendations: 
[121, 8819, 752, 7864, 8875, 925, 13988, 453, 18939, 22415]
recommending items to users:  3
using the generic recommender
recommendations: 
[20, 917, 56, 352, 58, 557, 21, 1911, 269, 22752]
recommending items to users:  4
using the generic recommender
recommendations: 
[23, 80, 124, 21, 68, 56, 436, 353, 61, 629]
recommending items to users:  5
using the cold recommender
recommendations: 
[25, 53, 21, 22, 124, 20, 23, 269, 353, 372]
recommending items to users:  6
using the generic recommender
recommendations: 
[1746, 23, 895, 56, 521, 61, 352, 27, 4297, 60]
recommending items to users:  7
using the generic recommender
recommendations: 
[1154, 21, 672, 

OSError: Cannot save file into a non-existent directory: 'Submissions'

In [10]:

test_users['item_list']= recommendations
test_users['item_list'] = pd.DataFrame([str(line).strip('[').strip(']').replace("'","") for line in test_users['item_list']])
test_users.to_csv('special_slim.csv', index=False)